# VGG Face2 Names

- add knowledge graph description with socre

In [39]:
%reload_ext autoreload
%autoreload 2

import os
from os.path import join
import math
from glob import glob
from random import randint

import numpy as np
import pandas as pd
%matplotlib inline
import matplotlib.pyplot as plt

import time
import datetime
import requests
import json
import urllib

import sys
sys.path.append('/work/megapixels_dev/megapixels/')
from app.utils import file_utils

In [43]:
DATA_STORE = '/data_store_nas/'
dir_dataset = join(DATA_STORE, 'datasets/people/vgg_face2')
fp_meta = join(dir_dataset, 'identity_meta_test.csv')

In [44]:
# load names
df_meta = pd.read_csv(fp_meta)
meta = df_meta.to_dict('index')
meta_orig = meta.copy()

In [57]:
# change first_last to first last
for idx, item in meta.items():
  name = item['name'].replace('_',' ')
  if '. ' in name[:3] and '. ' in name[2:6]:
    name = name[:6].replace('. ', '') + ' ' + name[6:]
  item['name'] = name

In [36]:
df_meta.head()

class_id              name  images  flag gender
0  n000001   14th_Dalai_Lama     424     0      m
1  n000002     A_Fine_Frenzy     315     1      f
2  n000003        A._A._Gill     205     1      m
3  n000004     A._J._Buckley     387     1      m
4  n000005  A._J._Pierzynski     229     1      m

In [58]:
api_key = open('/work/megapixels_dev/3rdparty/knowledge-graph-api/.api_key').read()

def get_knowledge(q, api_key):
  service_url = 'https://kgsearch.googleapis.com/v1/entities:search'
  params = {
      'query': q,
      'limit': 5,
      'indent': True,
      'key': api_key,
      }
  url = service_url + '?' + urllib.parse.urlencode(params)  # TODO: use requests
  response = json.loads(urllib.request.urlopen(url).read())
  response = response.get('itemListElement', [])
  if len(response) > 0:
    result = response[0].get('result', [])
    result['score'] = response[0]['resultScore']
    return result
  else:
    return []

In [60]:
# augment LFW CSV
for i in range(60):
  try:
    delay = 15
    keys = [('description','description'), ('name', 'name_kg'), ('url', 'url'), ('score', 'score')]
    for idx, item in meta.items():
      # check for empties unset
      try:
        _ = item['name_kg']
        continue
      except:
        pass
      
      kgr = get_knowledge(item['name'], api_key)
      for k1, k2 in keys:
        try:
          meta[idx][k2] = kgr[k1]
        except:
          meta[idx][k2] = ''
          #print('no {} data for {}'.format(k1, item['name']))
          pass
      #if idx % 10 == 0:
      txt = 'OK: {}, score: {}, desc: {}'.format(item['name'], meta[idx]['score'], meta[idx]['description'])
      time.sleep(1)
      txt += ', {} / {}, {:.2f}'.format(idx, len(meta), idx / len(meta))
      print(txt)
  except Exception as e:
    print(e, item['name'])
    time.sleep(60)
    pass

OK: AR Rahman, score: 465.11087, desc: Persian poet, 5 / 9131, 0.00
OK: A. Raja, score: 229.269058, desc: Educationist, 6 / 9131, 0.00
OK: AB de Villiers, score: 934.870728, desc: South African cricketer, 7 / 9131, 0.00
OK: AYAMI, score: 30.762762, desc: Japanese actress, 8 / 9131, 0.00
OK: Aamani, score: 35.454906, desc: Indian actress, 9 / 9131, 0.00
OK: Aamna Sharif, score: 452.583496, desc: Indian actress, 10 / 9131, 0.00
OK: Aaron Ashmore, score: 474.85495, desc: Canadian film actor, 11 / 9131, 0.00
OK: Aaron Hernandez, score: 584.928528, desc: Football tight end, 12 / 9131, 0.00
OK: Aaron Lennon, score: 523.926147, desc: Soccer player, 13 / 9131, 0.00
OK: Aaron Motsoaledi, score: 415.119965, desc: South African Minister of Health, 14 / 9131, 0.00
OK: Aaron Ramsey, score: 648.440491, desc: Soccer player, 15 / 9131, 0.00
OK: Aaron Rodgers, score: 846.989441, desc: Football quarterback, 16 / 9131, 0.00
OK: Aaron Schock, score: 474.634094, desc: Former United States Representative, 1

OK: Agnieszka Grochowska, score: 407.996613, desc: Polish actress, 108 / 9131, 0.01
OK: Agnieszka Maciag, score: 430.370483, desc: Model, 109 / 9131, 0.01
OK: Agnieszka Radwańska, score: 712.641785, desc: Polish tennis player, 110 / 9131, 0.01
OK: Agnieszka Wagner, score: 404.483246, desc: Polish actress, 111 / 9131, 0.01
OK: Agnieszka Włodarczyk, score: 477.707214, desc: Polish actress, 112 / 9131, 0.01
OK: Agnès Jaoui, score: 517.279846, desc: French actress, 113 / 9131, 0.01
OK: Agot Isidro, score: 442.114258, desc: Philippine singer, 114 / 9131, 0.01
OK: Agung Laksono, score: 374.144836, desc: Former Speaker of the Indonesian People's Representative Council, 115 / 9131, 0.01
OK: Agus Martowardojo, score: 370.383728, desc: Former Governor of Bank Indonesia, 116 / 9131, 0.01
OK: Agustina Cherri, score: 457.723877, desc: Argentine actress, 117 / 9131, 0.01
OK: Agustina Cordova, score: 350.110229, desc: Argentina actor, 118 / 9131, 0.01
OK: Agustín Carstens, score: 440.796295, desc: Ge

OK: Alejandro Escovedo, score: 490.664948, desc: American musician, 208 / 9131, 0.02
OK: Alejandro Falla, score: 450.014984, desc: Tennis player, 209 / 9131, 0.02
OK: Alejandro Fernández, score: 687.746094, desc: Mexican singer, 210 / 9131, 0.02
OK: Alejandro González Iñárritu, score: 959.804077, desc: Mexican film director, 211 / 9131, 0.02
OK: Alejandro Sabella, score: 551.713013, desc: Argentine football manager, 212 / 9131, 0.02
OK: Alejandro Sanz, score: 676.492676, desc: Spanish singer-songwriter, 213 / 9131, 0.02
OK: Alejandro Tous, score: 389.803589, desc: Spanish actor, 214 / 9131, 0.02
OK: Alejo Sauras, score: 429.060486, desc: Spanish actor, 215 / 9131, 0.02
OK: Alek Wek, score: 496.919037, desc: British-Sudanese model, 216 / 9131, 0.02
OK: Aleks Syntek, score: 525.40863, desc: Mexican singer-songwriter, 217 / 9131, 0.02
OK: Aleksandar Mitrović, score: 625.375, desc: Serbian soccer player, 218 / 9131, 0.02
OK: Aleksandar Vučić, score: 581.469116, desc: President of Serbia, 2

OK: Alfred Dorfer, score: 396.391327, desc: Austrian comedian, 308 / 9131, 0.03
OK: Alfred Schreuder, score: 388.103668, desc: Dutch soccer manager, 309 / 9131, 0.03
OK: Alfredo Pérez Rubalcaba, score: 693.995056, desc: Spanish Politician, 310 / 9131, 0.03
OK: Alfredo Talavera, score: 517.773376, desc: Mexican soccer player, 311 / 9131, 0.03
OK: Algirdas Butkevičius, score: 387.956787, desc: Former Prime Minister of Lithuania, 312 / 9131, 0.03
OK: Algirdas Šemeta, score: 337.248047, desc: Lithuanian economist, 313 / 9131, 0.03
OK: Ali Akbar Salehi, score: 648.754395, desc: Iranian diplomat, 314 / 9131, 0.03
OK: Ali Bastian, score: 410.652924, desc: Television actress, 315 / 9131, 0.03
OK: Ali Krieger, score: 524.43103, desc: American soccer player, 316 / 9131, 0.03
OK: Ali Michael, score: 425.161072, desc: American model, 317 / 9131, 0.03
OK: Ali al-Naimi, score: 542.232727, desc: , 318 / 9131, 0.03
OK: Alia Shawkat, score: 571.024109, desc: Actress, 319 / 9131, 0.03
OK: Alice Bah Kuhn

OK: Amrinder Gill, score: 559.298218, desc: Singer, 411 / 9131, 0.05
OK: Amruta Khanvilkar, score: 533.856873, desc: Indian film actress, 412 / 9131, 0.05
OK: Amy Acker, score: 561.301086, desc: , 413 / 9131, 0.05
OK: Amy Adams, score: 736.172607, desc: American actress, 414 / 9131, 0.05
OK: Amy Brenneman, score: 543.605591, desc: American actress, 415 / 9131, 0.05
OK: Amy Diamond, score: 489.061127, desc: Swedish singer, 416 / 9131, 0.05
OK: Amy Dumas, score: 429.785583, desc: American professional wrestler, 417 / 9131, 0.05
OK: Amy Fisher, score: 512.900146, desc: American writer, 418 / 9131, 0.05
OK: Amy Gumenick, score: 414.317963, desc: American actress, 419 / 9131, 0.05
OK: Amy Huberman, score: 435.558411, desc: Irish actress, 420 / 9131, 0.05
OK: Amy Paffrath, score: 441.600677, desc: American TV actress, 421 / 9131, 0.05
OK: Amy Pascal, score: 452.669128, desc: American business executive, 422 / 9131, 0.05
OK: Amy Robach, score: 522.433472, desc: Television presenter, 423 / 913

...

OK: Vicky Pryce, score: 378.624481, desc: Greek economist, 8713 / 9131, 0.95
OK: Victor Crivoi, score: 344.202942, desc: Romanian tennis player, 8714 / 9131, 0.95
OK: Victor Dubuisson, score: 416.654297, desc: French professional golfer, 8715 / 9131, 0.95
OK: Victor Garber, score: 575.156494, desc: Canadian actor, 8716 / 9131, 0.95
OK: Victor Moses, score: 610.84906, desc: Soccer player, 8717 / 9131, 0.95
OK: Victor Ortiz, score: 522.994019, desc: Professional boxer, 8718 / 9131, 0.95
OK: Victor Pițurcă, score: 547.767517, desc: Romanian football manager, 8719 / 9131, 0.95
OK: Victoria Abril, score: 554.829163, desc: Spanish film actress, 8720 / 9131, 0.95
OK: Victoria Gotti, score: 502.816711, desc: Writer, 8721 / 9131, 0.96
OK: Victoria Lopyreva, score: 491.844391, desc: Russian television presenter, 8722 / 9131, 0.96
OK: Victoria Pendleton, score: 538.754333, desc: Jockey, 8723 / 9131, 0.96
OK: Victoria Pratt, score: 447.128693, desc: Canadian actress, 8724 / 9131, 0.96
OK: Victoria

OK: Víctor Estrella Burgos, score: 646.31958, desc: Dominican tennis player, 8811 / 9131, 0.96
OK: Víctor Webster, score: 499.968048, desc: Canadian actor, 8812 / 9131, 0.97
OK: Vít Bárta, score: 345.53241, desc: Czech Politician, 8813 / 9131, 0.97
OK: Vítor Baía, score: 603.777466, desc: Portuguese soccer player, 8814 / 9131, 0.97
OK: Vítor Pereira, score: 482.900055, desc: Portuguese soccer player, 8815 / 9131, 0.97
OK: W. Brett Wilson, score: 516.17041, desc: Canadian businessman, 8816 / 9131, 0.97
OK: Wael Kfoury, score: 520.938232, desc: Lebanese singer, 8817 / 9131, 0.97
OK: Waldemar Fornalik, score: 464.599182, desc: Polish soccer player, 8818 / 9131, 0.97
OK: Walid Jumblatt, score: 446.835907, desc: Lebanese Politician, 8819 / 9131, 0.97
OK: Wallace Huo, score: 557.564026, desc: Actor, 8820 / 9131, 0.97
OK: Walt Mossberg, score: 365.500458, desc: American journalist, 8821 / 9131, 0.97
OK: Walter Mazzarri, score: 519.551636, desc: Italian soccer player, 8822 / 9131, 0.97
OK: Wal

OK: Yang Yuanqing, score: 379.713867, desc: Chairman of Lenovo Group, 8911 / 9131, 0.98
OK: Yani Tseng, score: 477.128479, desc: Taiwanese professional golfer, 8912 / 9131, 0.98
OK: Yanina Wickmayer, score: 538.386353, desc: Belgian tennis player, 8913 / 9131, 0.98
OK: Yann Moix, score: 507.245575, desc: French author, 8914 / 9131, 0.98
OK: Yann Sommer, score: 593.007751, desc: Soccer player, 8915 / 9131, 0.98
OK: Yannick Agnel, score: 482.159576, desc: French swimmer, 8916 / 9131, 0.98
OK: Yannick Bisson, score: 484.713715, desc: Canadian film actor, 8917 / 9131, 0.98
OK: Yannick Noah, score: 642.409485, desc: Tennis player, 8918 / 9131, 0.98
OK: Yarisley Silva, score: 399.162109, desc: Cuban olympic athlete, 8919 / 9131, 0.98
OK: Yaroslava Shvedova, score: 478.185028, desc: Kazakhstani-Russian tennis player, 8920 / 9131, 0.98
OK: Yasmin Brunet, score: 474.12262, desc: Brazilian model, 8921 / 9131, 0.98
OK: Yasmin Le Bon, score: 647.195557, desc: Model, 8922 / 9131, 0.98
OK: Yasmin Wa

OK: Zbigniew Ziobro, score: 462.645142, desc: Polish Politician, 9011 / 9131, 0.99
OK: Zdena Studenkova, score: 430.441101, desc: Film actress, 9012 / 9131, 0.99
OK: Zdenka Predná, score: 374.726105, desc: Slovak singer, 9013 / 9131, 0.99
OK: Zdeněk Troška, score: 394.861603, desc: Film director, 9014 / 9131, 0.99
OK: Zdeněk Zeman, score: 623.512634, desc: Football coach, 9015 / 9131, 0.99
OK: Zendaya, score: 60.110863, desc: American actress, 9016 / 9131, 0.99
OK: Zeynep Sever, score: 472.091858, desc: Belgian-Turkish volleyball player, 9017 / 9131, 0.99
OK: Zhang Dejiang, score: 490.977905, desc: Chinese Politician, 9018 / 9131, 0.99
OK: Zhang Jingchu, score: 487.140686, desc: Chinese film actress, 9019 / 9131, 0.99
OK: Zhang Xin, score: 409.479065, desc: CEO of SOHO China, 9020 / 9131, 0.99
OK: Zheng Saisai, score: 530.717102, desc: Chinese tennis player, 9021 / 9131, 0.99
OK: Zhou Dongyu, score: 513.390015, desc: Chinese actress, 9022 / 9131, 0.99
OK: Zinedine Zidane, score: 1087.8

OK: Šárka Vaňková, score: 361.424988, desc: Czech singer, 9113 / 9131, 1.00
OK: Željko Obradović, score: 521.944092, desc: Basketball coach, 9114 / 9131, 1.00
OK: Žydrūnas Savickas, score: 526.85675, desc: Lithuanian strongman, 9115 / 9131, 1.00
OK: Наталья Могилевская, score: 10.55209, desc: TV show, 9116 / 9131, 1.00
HTTP Error 503: Service Unavailable 孫耀威
HTTP Error 503: Service Unavailable 孫耀威
HTTP Error 503: Service Unavailable 孫耀威
HTTP Error 503: Service Unavailable 孫耀威
OK: 孫耀威, score: 5.982057, desc: Actor, 9117 / 9131, 1.00
OK: 宮本佳林, score: 103.06398, desc: Japanese idol, 9118 / 9131, 1.00
OK: 松井友里絵, score: , desc: , 9119 / 9131, 1.00
OK: 神戸蘭子, score: , desc: , 9120 / 9131, 1.00
OK: 裕美, score: 11.073155, desc: Japanese singer-songwriter, 9121 / 9131, 1.00
OK: 馬場典子, score: 39.904381, desc: Former soccer player, 9122 / 9131, 1.00
OK: Jackie Chan, score: 871.680237, desc: Martial artist, 9123 / 9131, 1.00
OK: Pei-pei Cheng, score: 525.495056, desc: Actress, 9124 / 9131, 1.00
OK: R

In [68]:
df_meta_desc = pd.DataFrame.from_dict(list(meta.values()))

In [69]:
fp_out = '/data_store/datasets/people/vgg_face2/identity_meta_kg.csv'

In [70]:
df_meta_desc.to_csv(fp_out)